# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model loaded [TRPO]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
from google.colab import drive
drive.mount('/content/drive')

%cd /content/drive/MyDrive/DAI-Labor/RL_VPP_Thesis/
%ls

Mounted at /content/drive
/content/drive/MyDrive/DAI-Labor/RL_VPP_Thesis
Agent_trainer_notebooks/          README.md             VPP_environment.py
data/                             Simulator_notebooks/  VPP_simulator.ipynb
Hyperparameters_sweep_notebooks/  trained_models/       wandb/


In [3]:
# #Cloning repository and changing directory
# !git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
# %cd RL_VPP_Thesis/
# %ls

In [4]:
import yaml
import numpy as np
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import TRPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')
wandb, version 0.13.4


In [5]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [6]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 65% average battery) 
#case = 'wohnblock_household_simulation_adaptive_18.yaml' #(18 EVs arrivals per week with 40% average battery) 
#case = 'wohnblock_household_simulation_adaptive_22.yaml' #(22 EVs arrivals per week with 55% average battery)

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7fb2b022e750>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 20
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 20, 'EVs_n_max': 1044, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [7]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [8]:
env.plot_ELVIS_data()

In [9]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  22127.74 , over-consume=kWh  39023.53 , under-consume=kWh  16895.78 , Total_cost=€  887.05 , overcost=€  1377.1 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [10]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [12]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [13]:
env.plot_VPP_Elvis_comparison()

In [14]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
env.plot_rewards_stats()

In [16]:
env.plot_EVs_kpi()

In [17]:
env.plot_actions_kpi()

In [18]:
env.plot_load_kpi()

In [19]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [20]:
## Wandb login to load models
#In Colab, uncomment below:
%env "WANDB_DISABLE_CODE" True
%env "WANDB_NOTEBOOK_NAME" "Simulator_notebooks/TRPO_VPP_simulator.ipynb"
os.environ['WANDB_NOTEBOOK_NAME'] = 'Simulator_notebooks/TRPO_VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

env: "WANDB_DISABLE_CODE"=True
env: "WANDB_NOTEBOOK_NAME"="Simulator_notebooks/TRPO_VPP_simulator.ipynb"


In [21]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/TRPO_models/model_TRPO_"

model_id = "2ydih28d"
model = TRPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

## Testing dataset VPP Simulation using the loaded trained model

In [22]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  22302.74 , over-consume=kWh  39633.4 , under-consume=kWh  17330.65 , Total_cost=€  872.68 , overcost=€  1372.11 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -5018.84 , over-consume=KWh  1683.14 , under-consume=KWh  6701.98 , Total_cost=€  -119.26 , Overcost=€  58.35 
 EV_INFO: Av.EV_energy_leaving=kWh  65.31 , Std.EV_energy_leaving=kWh  26.96 , EV_departures =  1043 , EV_queue_left =  0
SCORE:  Cumulative_reward= 357845.95 - Step_rewars (load_t= 334319.55, EVs_energy_t= 1606.58)
 - Final_rewards (EVs_energy= 14417.29, Overconsume= -917.05, Underconsume= -3500.86, Overcost= 11920.44)
Episode:1 Score:357845.9455449787


In [23]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [24]:
VPP_table.head(15000)

0          1    2          3  \
time                                                        
2022-01-01 00:00:00  63.119423  55.207069  0.0  56.269512   
2022-01-01 00:15:00  62.869423  54.957069  0.0  56.019512   
2022-01-01 00:30:00  62.522198  54.609844  0.0  56.269512   
2022-01-01 00:45:00  62.168159  54.255806  0.0  56.519512   
2022-01-01 01:00:00  61.813393  53.901039  0.0  56.769512   
...                        ...        ...  ...        ...   
2022-06-06 04:45:00   0.000000  99.668655  0.0  90.929588   
2022-06-06 05:00:00   0.000000  99.989998  0.0  92.429985   
2022-06-06 05:15:00   0.000000  99.989998  0.0  93.897720   
2022-06-06 05:30:00   0.000000  99.989998  0.0  95.289665   
2022-06-06 05:45:00   0.000000  99.989998  0.0  96.783493   

                                    EVs_id       actions  \
time                                                       
2022-01-01 00:00:00           [0, 0, 0, 0]  [2, 2, 2, 2]   
2022-01-01 00:15:00  [3127, 3129, 0, 3128]  [2, 2, 2, 1]   
2022-01-01 00:30:00  [3127, 3129, 0, 3128]  [2, 2, 2, 1]   
2022-01-01 00:45:00  [3127, 3129, 0, 3128]  [2, 2, 2, 1]   
2022-01-01 01:00:00  [3127, 3129, 0, 3128]  [2, 2, 2, 1]   
...                                    ...           ...   
2022-06-06 04:45:00     [0, 3555, 0, 3554]  [0, 1, 0, 1]   
2022-06-06 05:00:00     [0, 3555, 0, 3554]  [0, 1, 2, 1]   
2022-06-06 05:15:00     [0, 3555, 0, 3554]  [0, 1, 2, 1]   
2022-06-06 05:30:00     [0, 3555, 0, 3554]  [0, 1, 0, 1]   
2022-06-06 05:45:00     [0, 3555, 0, 3554]  [0, 1, 2, 1]   

                                       mask_truth          load  load_reward  \
time                                                                           
2022-01-01 00:00:00  [False, False, False, False]  1.811884e+00     8.510917   
2022-01-01 00:15:00    [True, True, False, False] -4.326055e-01    15.000000   
2022-01-01 00:30:00    [True, True, False, False]  0.000000e+00    15.000000   
2022-01-01 00:45:00    [True, True, False, False]  0.000000e+00    15.000000   
2022-01-01 01:00:00    [True, True, False, False] -2.220446e-16    15.000000   
...                                           ...           ...          ...   
2022-06-06 04:45:00     [True, False, True, True]  0.000000e+00    -5.651108   
2022-06-06 05:00:00    [True, False, False, True] -4.716218e+00    -6.700857   
2022-06-06 05:15:00    [True, False, False, True] -5.870942e+00    -6.425259   
2022-06-06 05:30:00     [True, False, True, True] -5.567785e+00    -6.795732   
2022-06-06 05:45:00    [True, False, False, True] -5.975305e+00    -7.107516   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0   8.510917  
2022-01-01 00:15:00        0.0  15.000000  
2022-01-01 00:30:00        0.0  15.000000  
2022-01-01 00:45:00        0.0  15.000000  
2022-01-01 01:00:00        0.0  15.000000  
...                        ...        ...  
2022-06-06 04:45:00        0.0  -5.651108  
2022-06-06 05:00:00        0.0  -6.700857  
2022-06-06 05:15:00        0.0  -6.425259  
2022-06-06 05:30:00        0.0  -6.795732  
2022-06-06 05:45:00        0.0  -7.107516  

[15000 rows x 11 columns]

In [25]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [26]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [27]:
env.plot_VPP_Elvis_comparison()

In [28]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [29]:
env.plot_rewards_stats()

In [30]:
env.plot_EVs_kpi()

In [31]:
env.plot_load_kpi()

In [32]:
env.plot_yearly_load_log()

## Validating dataset VPP Simulation using the loaded trained model

In [33]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 4173, Arrival time: 2022-01-01 08:45:00, Parking_time: 24, Leaving_time: 2022-01-02 08:45:00, SOC: 0.5199514781779078, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 5215, Arrival time: 2022-12-31 18:15:00, Parking_time: 24, Leaving_time: 2023-01-01 18:15:00, SOC: 0.4715967787601019, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13044.07 , over-consume=kWh  34553.22 , under-consume=kWh  21509.15 , Total_cost=€  626.18 , overcost=€  1504.65 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89


In [34]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

In [35]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = TRPO.load(RecurrentPPO_path + model_id, env=env)

In [36]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12278.52 , over-consume=kWh  33850.42 , under-consume=kWh  21571.9 , Total_cost=€  623.33 , overcost=€  1497.16 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -7496.07 , over-consume=KWh  1156.66 , under-consume=KWh  8652.73 , Total_cost=€  -298.48 , Overcost=€  49.52 
 EV_INFO: Av.EV_energy_leaving=kWh  72.06 , Std.EV_energy_leaving=kWh  26.43 , EV_departures =  1037 , EV_queue_left =  2
SCORE:  Cumulative_reward= 366873.42 - Step_rewars (load_t= 318819.29, EVs_energy_t= 20129.02)
 - Final_rewards (EVs_energy= 18558.24, Overconsume= -578.35, Underconsume= -3770.83, Overcost= 13716.06)
Episode:1 Score:366873.42471367965


In [37]:
env.plot_VPP_energies()

In [38]:
VPP_table.head(15000)

0    1          2    3              EVs_id  \
time                                                                      
2022-01-01 00:00:00   0.000000  0.0   0.000000  0.0        [0, 0, 0, 0]   
2022-01-01 00:15:00   0.000000  0.0   0.000000  0.0        [0, 0, 0, 0]   
2022-01-01 00:30:00   0.000000  0.0   0.000000  0.0        [0, 0, 0, 0]   
2022-01-01 00:45:00   0.000000  0.0   0.000000  0.0        [0, 0, 0, 0]   
2022-01-01 01:00:00   0.000000  0.0   0.000000  0.0        [0, 0, 0, 0]   
...                        ...  ...        ...  ...                 ...   
2022-06-06 04:45:00  64.719673  0.0  39.008385  0.0  [6715, 0, 6714, 0]   
2022-06-06 05:00:00  66.544014  0.0  40.832722  0.0  [6715, 0, 6714, 0]   
2022-06-06 05:15:00  68.151497  0.0  42.440208  0.0  [6715, 0, 6714, 0]   
2022-06-06 05:30:00  69.886673  0.0  44.175385  0.0  [6715, 0, 6714, 0]   
2022-06-06 05:45:00  71.660812  0.0  45.949524  0.0  [6715, 0, 6714, 0]   

                          actions                   mask_truth      load  \
time                                                                       
2022-01-01 00:00:00  [1, 0, 2, 1]  [False, True, False, False] -3.515241   
2022-01-01 00:15:00  [1, 0, 2, 1]  [False, True, False, False] -2.839915   
2022-01-01 00:30:00  [1, 0, 2, 1]  [False, True, False, False] -3.463300   
2022-01-01 00:45:00  [1, 0, 2, 1]  [False, True, False, False] -3.487851   
2022-01-01 01:00:00  [1, 0, 2, 1]  [False, True, False, False] -3.892018   
...                           ...                          ...       ...   
2022-06-06 04:45:00  [1, 0, 1, 0]     [True, True, True, True]  0.000000   
2022-06-06 05:00:00  [1, 0, 1, 0]     [True, True, True, True]  0.000000   
2022-06-06 05:15:00  [1, 0, 1, 0]     [True, True, True, True]  0.000000   
2022-06-06 05:30:00  [1, 0, 1, 0]     [True, True, True, True]  0.000000   
2022-06-06 05:45:00  [1, 0, 1, 0]     [True, True, True, True]  0.000000   

                     load_reward  EV_reward    rewards  
time                                                    
2022-01-01 00:00:00    -3.066525        0.0  -3.066525  
2022-01-01 00:15:00    -4.105500        0.0  -4.105500  
2022-01-01 00:30:00    -4.146418        0.0  -4.146418  
2022-01-01 00:45:00    -4.820030        0.0  -4.820030  
2022-01-01 01:00:00    -4.128438        0.0  -4.128438  
...                          ...        ...        ...  
2022-06-06 04:45:00    15.000000        0.0  15.000000  
2022-06-06 05:00:00    15.000000        0.0  15.000000  
2022-06-06 05:15:00    15.000000        0.0  15.000000  
2022-06-06 05:30:00    15.000000        0.0  15.000000  
2022-06-06 05:45:00    15.000000        0.0  15.000000  

[15000 rows x 11 columns]

In [39]:
env.plot_VPP_results()


In [40]:
env.plot_VPP_Elvis_comparison()

In [41]:
env.plot_rewards_results()

In [42]:
env.plot_rewards_stats()

In [43]:
env.plot_EVs_kpi()

In [44]:
env.plot_load_kpi()

In [45]:
env.plot_yearly_load_log()

## Training dataset VPP Simulation using the loaded trained model

In [46]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 7302, Arrival time: 2022-01-01 14:00:00, Parking_time: 22.387843078043385, Leaving_time: 2022-01-02 12:23:16.235081, SOC: 0.5698980096002337, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 8344, Arrival time: 2022-12-31 08:30:00, Parking_time: 24, Leaving_time: 2023-01-01 08:30:00, SOC: 0.49454196240535986, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8834.1 , over-consume=kWh  32289.78 , under-consume=kWh  23455.68 , Total_cost=€  489.09 , overcost=€  1352.94 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2


In [47]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [48]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = TRPO.load(RecurrentPPO_path + model_id, env=env)

In [49]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8981.14 , over-consume=kWh  32398.56 , under-consume=kWh  23417.42 , Total_cost=€  519.65 , overcost=€  1372.22 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -9549.68 , over-consume=KWh  1180.5 , under-consume=KWh  10730.18 , Total_cost=€  -325.51 , Overcost=€  49.26 
 EV_INFO: Av.EV_energy_leaving=kWh  73.67 , Std.EV_energy_leaving=kWh  26.39 , EV_departures =  1042 , EV_queue_left =  0
SCORE:  Cumulative_reward= 336357.56 - Step_rewars (load_t= 290086.3, EVs_energy_t= 20918.75)
 - Final_rewards (EVs_energy= 17685.91, Overconsume= -670.89, Underconsume= -4841.5, Overcost= 13178.99)
Episode:1 Score:336357.5563522922


In [50]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [51]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  36.373997  99.989998  83.783180  84.609680   
2022-06-06 05:00:00  36.123997  99.989998  84.681938  85.508438   
2022-06-06 05:15:00  36.123997  99.989998  85.514793  86.341293   
2022-06-06 05:30:00  36.123997  99.989998  86.321022  87.147522   
2022-06-06 05:45:00  36.123997  99.989998  87.083946  87.910446   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [1, 0, 2, 1]   
...                                       ...           ...   
2022-06-06 04:45:00  [9854, 9851, 9852, 9853]  [2, 1, 1, 1]   
2022-06-06 05:00:00  [9854, 9851, 9852, 9853]  [0, 1, 1, 1]   
2022-06-06 05:15:00  [9854, 9851, 9852, 9853]  [0, 1, 1, 1]   
2022-06-06 05:30:00  [9854, 9851, 9852, 9853]  [0, 1, 1, 1]   
2022-06-06 05:45:00  [9854, 9851, 9852, 9853]  [0, 1, 1, 1]   

                                      mask_truth      load  load_reward  \
time                                                                      
2022-01-01 00:00:00  [False, True, False, False] -4.011733    -5.041318   
2022-01-01 00:15:00  [False, True, False, False] -4.045449    -5.689719   
2022-01-01 00:30:00  [False, True, False, False] -4.758691    -3.874312   
2022-01-01 00:45:00  [False, True, False, False] -3.324587    -6.427478   
2022-01-01 01:00:00  [False, True, False, False] -5.570226    -6.350144   
...                                          ...       ...          ...   
2022-06-06 04:45:00   [False, False, True, True] -2.407461    -4.325062   
2022-06-06 05:00:00   [False, False, True, True] -3.595037    -3.885712   
2022-06-06 05:15:00   [False, False, True, True] -3.331427    -3.708180   
2022-06-06 05:30:00   [False, False, True, True] -3.224908    -3.419495   
2022-06-06 05:45:00   [False, False, True, True] -3.051697    -4.524720   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -5.041318  
2022-01-01 00:15:00        0.0  -5.689719  
2022-01-01 00:30:00        0.0  -3.874312  
2022-01-01 00:45:00        0.0  -6.427478  
2022-01-01 01:00:00        0.0  -6.350144  
...                        ...        ...  
2022-06-06 04:45:00        0.0  -4.325062  
2022-06-06 05:00:00        0.0  -3.885712  
2022-06-06 05:15:00        0.0  -3.708180  
2022-06-06 05:30:00        0.0  -3.419495  
2022-06-06 05:45:00       50.1  45.575280  

[15000 rows x 11 columns]

In [52]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [53]:
env.plot_VPP_Elvis_comparison()

In [54]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [55]:
env.plot_rewards_stats()

In [56]:
env.plot_EVs_kpi()

In [57]:
env.plot_actions_kpi()

In [58]:
env.plot_load_kpi()

In [59]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [60]:
#env.close()